In [1]:
import time, requests, re
from urllib.parse import urlparse
from bs4 import BeautifulSoup
from tqdm.notebook import tqdm
from collections import defaultdict
from tweepy import OAuthHandler, API

from urllib.parse import parse_qs, quote, unquote, urlparse
import pandas as pd
import pprint
import json

from difflib import SequenceMatcher
import time, requests, re, random, tldextract

from googleapiclient.discovery import build


In [2]:
import yaml, os
directory_path = "D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/"

# load config_KEYS.yaml file
with open(os.path.join(directory_path, "utility/config_KEYS.yml"), "r") as ymlfile:
    cfg =  yaml.safe_load(ymlfile)

In [3]:
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [4]:
pp = pprint.PrettyPrinter(width=41, compact=True)

In [5]:
# Authenticate to Twitter
# Authenticate to Twitter
auth = OAuthHandler(cfg["API_KEYS"], cfg["API_SECRET_KEYS"])
auth.set_access_token(cfg["ACCESS_TOKEN"], cfg["ACCESS_TOKEN_SECRET"])

api = API(auth)

if api.verify_credentials() == False:
    print("The user credentials are invalid.")
else:
    print("The user credentials are valid.")

The user credentials are valid.


In [6]:
# Authenticate to youtube
youtube_service = build('youtube', 'v3', developerKey=cfg["YOUTUBE_KEY"])

pages to scrap for list of news channels.

https://mediabiasfactcheck.com/left/  <Br>
https://mediabiasfactcheck.com/leftcenter/ <Br>
https://mediabiasfactcheck.com/center/ <Br>
https://mediabiasfactcheck.com/right-center/ <Br>
https://mediabiasfactcheck.com/right/ <Br>

https://mediabiasfactcheck.com/fake-news/ <Br>

In [7]:
headers = requests.utils.default_headers()

headers.update(
    {
        'User-Agent': 'My User Agent 1.0',
    }
)

In [17]:
ideology_pages = ['left', 'leftcenter', 'center', 'right-center', 'right', 'fake-news']
bias_rating = ['left', 'center-left', 'center', 'center-right', 'right', 'fake-news']

links = []
names = []
bias_ratings = []
for i, pages in enumerate(ideology_pages):
    tags_ignored = 0
    
    MBFC_SOURCE_URL = "https://mediabiasfactcheck.com/{}/".format(pages)
    #print(MBFC_SOURCE_URL)
    response = requests.get(MBFC_SOURCE_URL)
    soup = BeautifulSoup(response.text, 'lxml')

    #list_pages = soup.find( "table", {"id":"mbfc-table"} ).find_all("tr")
    table = soup.find('table', attrs={'id':'mbfc-table'}).find("tbody")
    list_rows = table.find_all('tr')


    for row_idx, row in enumerate(list_rows):
        try:
            link = row.find('td').find('a', href=True).get('href')
            name = row.find('td').text
            
            names.append(name)
            links.append(link)
            bias_ratings.append(bias_rating[i])
            
        except:
            tags_ignored += 1
            #print("ignoring one tag")
    #news_channel_list = news_channel_list.reset_index(drop=True)
    print("Tags ignored for {} ideology news channels list: {}".format(pages, tags_ignored))

news_channel_list = pd.DataFrame(
    {'Name': names,
     'Link': links,
     'Bias Rating': bias_ratings,
     'Country': None,
     'Website': None
    })
    
# requesting each websites
for j, link in enumerate(news_channel_list["Link"]):
    #link = "https://mediabiasfactcheck.com/american-united-separation-church-state/"
    response = requests.get(link)
    soup = BeautifulSoup(response.text, 'lxml')

    # get the p tag with Bias Rating and country.
    news_info = soup.find("div", {"class" : "entry-content clearfix"})

    try:
        news_channel_information = news_info.find_all(text = re.compile('Country:'))[0].parent.get_text(strip=False).split("\n")

        for n_i in news_channel_information:
            if n_i.split(":")[0] == "Country":
                country = n_i.split(":")[1].strip()
                if country != "":
                    #country.append(n_i.split(":")[1].strip() )
                    news_channel_list.loc[j, "Country"] = country
                else:
                    #print("country is empty")
                    raise 

        print("News channel Index : ", j, " Done!")
    except:
        country_ = "NA"
        country_pattern = r'Country:\s[a-zA-Z]+'
        try:
            for line in news_info.text.split('\n'):
                if bool(re.match(country_pattern, line)):
                    #country = line.rstrip().split(':')[1].split('(')[0].strip()
                    country_ = line.split(":")[1].strip()
                    #country.append(country_)
                    news_channel_list.loc[j, "Country"] = country_

            if country_ == "NA":
                print("News channel Index : ", j, " Not Done!")
            else:
                print("News channel Index : ", j, " Done by 2nd method!")
        except:
            print("The MBFC website for {} does not exists!".format(news_channel_list["Name"][j]))

    try:
        source = news_info.find_all(text = re.compile('Source:'))[0].parent.find('a', href=True).get('href')
        #news_website.append(source)
        news_channel_list.loc[j, "Website"] = source
        print("News Channel source for Index : ", j, " Done!")

    except:
        source_ = "NA"
        source_pattern = r'Sources?:\shttps?://(?:[-\w.]|(?:%[\da-fA-F]{2}))+'
        try:
            for line in news_info.text.split('\n'):
                if bool(re.match(source_pattern, line)):
                    source_ = line.split(":", 1)[1].strip().rstrip(" ")
                    #news_website.append(source_)
                    news_channel_list.loc[j, "Website"] = source_

            if source_ == "NA":
                print("News channel source Index : ", j, " Not Done!")
            else:
                print("News channel source Index : ", j, " Done by 2nd method!")
        except:
            print("The MBFC website for {} does not exists!".format(news_channel_list["Name"][j]))


ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
ignoring one tag
News channel Index :  0  Done!
News Channel source for Index :  0  Done!
News channel Index :  1  Done!
News Channel source for Index :  1  Done!
News channel Index :  2  Done!
News Channel source for Index :  2  Done!
News channel Index :  3  Done!
News Channel source for Index :  3  Done!
News channel Index :  4  Done!
News Channel source for Index :  4  Done!
News channel Index :  5  Done!
News Channel source for In

News channel Index :  101  Done!
News Channel source for Index :  101  Done!
News channel Index :  102  Done!
News Channel source for Index :  102  Done!
News channel Index :  103  Done!
News Channel source for Index :  103  Done!
News channel Index :  104  Done!
News Channel source for Index :  104  Done!
News channel Index :  105  Done!
News Channel source for Index :  105  Done!
News channel Index :  106  Done!
News Channel source for Index :  106  Done!
News channel Index :  107  Done!
News Channel source for Index :  107  Done!
News channel Index :  108  Done!
News Channel source for Index :  108  Done!
News channel Index :  109  Done!
News Channel source for Index :  109  Done!
News channel Index :  110  Done!
News Channel source for Index :  110  Done!
News channel Index :  111  Done by 2nd method!
News Channel source for Index :  111  Done!
News channel Index :  112  Done!
News Channel source for Index :  112  Done!
News channel Index :  113  Done!
News Channel source for Index

News channel Index :  206  Done!
News Channel source for Index :  206  Done!
News channel Index :  207  Done!
News Channel source for Index :  207  Done!
News channel Index :  208  Done!
News Channel source for Index :  208  Done!
News channel Index :  209  Done!
News Channel source for Index :  209  Done!
News channel Index :  210  Done!
News Channel source for Index :  210  Done!
News channel Index :  211  Done!
News Channel source for Index :  211  Done!
News channel Index :  212  Done!
News Channel source for Index :  212  Done!
News channel Index :  213  Done!
News Channel source for Index :  213  Done!
News channel Index :  214  Done!
News Channel source for Index :  214  Done!
News channel Index :  215  Done!
News Channel source for Index :  215  Done!
News channel Index :  216  Done!
News Channel source for Index :  216  Done!
News channel Index :  217  Done!
News Channel source for Index :  217  Done!
News channel Index :  218  Done!
News Channel source for Index :  218  Done!

News channel Index :  311  Done!
News Channel source for Index :  311  Done!
News channel Index :  312  Done!
News Channel source for Index :  312  Done!
News channel Index :  313  Done!
News Channel source for Index :  313  Done!
News channel Index :  314  Done!
News Channel source for Index :  314  Done!
News channel Index :  315  Done!
News Channel source for Index :  315  Done!
News channel Index :  316  Done!
News Channel source for Index :  316  Done!
News channel Index :  317  Done!
News Channel source for Index :  317  Done!
News channel Index :  318  Done!
News Channel source for Index :  318  Done!
News channel Index :  319  Done!
News Channel source for Index :  319  Done!
News channel Index :  320  Done!
News Channel source for Index :  320  Done!
News channel Index :  321  Done!
News Channel source for Index :  321  Done!
News channel Index :  322  Done by 2nd method!
News Channel source for Index :  322  Done!
News channel Index :  323  Done!
News Channel source for Index

News channel Index :  418  Done!
News Channel source for Index :  418  Done!
News channel Index :  419  Done!
News Channel source for Index :  419  Done!
News channel Index :  420  Done!
News Channel source for Index :  420  Done!
News channel Index :  421  Done!
News Channel source for Index :  421  Done!
News channel Index :  422  Done!
News Channel source for Index :  422  Done!
News channel Index :  423  Done!
News Channel source for Index :  423  Done!
News channel Index :  424  Done!
News Channel source for Index :  424  Done!
News channel Index :  425  Done!
News Channel source for Index :  425  Done!
News channel Index :  426  Done!
News Channel source for Index :  426  Done!
News channel Index :  427  Done!
News Channel source for Index :  427  Done!
News channel Index :  428  Done!
News Channel source for Index :  428  Done!
News channel Index :  429  Done!
News Channel source for Index :  429  Done!
News channel Index :  430  Done!
News Channel source for Index :  430  Done!

News channel Index :  523  Done by 2nd method!
News Channel source for Index :  523  Done!
News channel Index :  524  Done by 2nd method!
News Channel source for Index :  524  Done!
News channel Index :  525  Done!
News Channel source for Index :  525  Done!
News channel Index :  526  Not Done!
News channel source Index :  526  Not Done!
News channel Index :  527  Done!
News Channel source for Index :  527  Done!
News channel Index :  528  Done!
News Channel source for Index :  528  Done!
News channel Index :  529  Done!
News Channel source for Index :  529  Done!
News channel Index :  530  Done!
News Channel source for Index :  530  Done!
News channel Index :  531  Done!
News Channel source for Index :  531  Done!
News channel Index :  532  Done by 2nd method!
News Channel source for Index :  532  Done!
News channel Index :  533  Done!
News Channel source for Index :  533  Done!
News channel Index :  534  Done!
News Channel source for Index :  534  Done!
News channel Index :  535  Don

News channel Index :  627  Done!
News Channel source for Index :  627  Done!
News channel Index :  628  Done!
News Channel source for Index :  628  Done!
News channel Index :  629  Done by 2nd method!
News Channel source for Index :  629  Done!
News channel Index :  630  Done!
News Channel source for Index :  630  Done!
News channel Index :  631  Done!
News Channel source for Index :  631  Done!
News channel Index :  632  Done!
News Channel source for Index :  632  Done!
News channel Index :  633  Done!
News Channel source for Index :  633  Done!
News channel Index :  634  Done!
News Channel source for Index :  634  Done!
News channel Index :  635  Done!
News Channel source for Index :  635  Done!
News channel Index :  636  Done!
News Channel source for Index :  636  Done!
News channel Index :  637  Done!
News channel source Index :  637  Not Done!
News channel Index :  638  Done!
News Channel source for Index :  638  Done!
News channel Index :  639  Done!
News Channel source for Index

AttributeError: 'NoneType' object has no attribute 'text'

In [45]:
links = []
names = []
bias_ratings = []

tags_ignored = 0
MBFC_SOURCE_URL = "https://mediabiasfactcheck.com/{}/".format("fake-news")
#print(MBFC_SOURCE_URL)
response = requests.get(MBFC_SOURCE_URL)
soup = BeautifulSoup(response.text, 'lxml')

#list_pages = soup.find( "table", {"id":"mbfc-table"} ).find_all("tr")
table = soup.find('table', attrs={'id':'mbfc-table'}).find("tbody")
list_rows = table.find_all('tr')

for row_idx, row in tqdm(enumerate(list_rows)):
    try:
        link = row.find('td').find('a', href=True).get('href')
        name = row.find('td').text

        names.append(name)
        links.append(link)
        bias_ratings.append(bias_rating[i])

    except:
        tags_ignored += 1
        #print("ignoring one tag")
#news_channel_list = news_channel_list.reset_index(drop=True)
print("Tags ignored for {} ideology news channels list: {}".format("fake-news", tags_ignored))

news_channel_list = pd.DataFrame(
    {'Name': names,
     'Link': links,
     #'Bias Rating': bias_ratings,
     #'Country': None,
     #'Website': None
    })


945it [00:00, 27001.04it/s]

Tags ignored for fake-news ideology news channels list: 945


In [51]:
news_channel_list

Name  \
0    2nd Amendment Daily News (secondamendmentdaily...   
1                                            4Chan.org   
2                    100% Fed up (100percentfedup.com)   
3                                        12minutos.com   
4                                          24Jours.com   
5                              24 News (us24news.com/)   
6             2020 Conservative (2020conservative.com)   
7               A Voice for Men (www.avoiceformen.com)   
8                          Acting Man (Acting-man.com)   
9                                        Action News 3   
10                  Activist Mommy (activistmommy.com)   
11                      Ada Reporter (adareporter.com)   
12           Adams County Times (adamscountytimes.com)   
13                  Al Arabiya (english.alarabiya.net)   
14                Albany Standard (albanystandard.com)   
15                        Al Bawaba (www.albawaba.com)   
16             All News Pipeline (allnewspipeline.com)   
17       Alliance Defending Freedom (www.adflegal.org)   
18                   Al Manar (english.almanar.com.lb)   
19                  Al- Masdar News (almasdarnews.com)   
20               Aloha State News (alohastatenews.com)   
21                        Alpha News (alphanewsmn.com)   
22                                        Alt-Right TV   
23                      Al Youm Al Sabea (youm7.com)\n   
24                    America Daily (americadaily.com)   
25               America Max News (americamaxnews.com)   
26       American Action News (americanactionnews.com)   
27   American College of Pediatricians (www.acpeds....   
28   American Conservative Media (americanconservat...   
29   American Conservative Movement (americanconser...   
30           American Family Association (www.afa.net)   
31                    American Family News (afn.net)\n   
32   American Freedom Fighters (www.americasfreedom...   
33                  American Gulag (americangulag.org)   
34   American Liberty Report (www.americanlibertyre...   
35              American Lookout (americanlookout.com)   
36   American Patriot Daily (www.americanpatriotdai...   
37     American People Daily (americanpeopledaily.com)   
38   American Principles Project (americanprinciple...   
39       American Renaissance Magazine (www.amren.com)   
40   American Society for the Defense of Tradition,...   
41          American Thinker (www.americanthinker.com)   
42       American Truth Today (americantruthtoday.com)   
43                  American Web Media (AWM) (awm.com)   
44       Americans Are Pissed (americansarepissed.com)   
45   Americans for Truth (https://americansfortruth...   
46      America’s News Source (americasnewssource.com)   
47                          Ames Today (amestoday.com)   
48            Analyzing America (analyzingamerica.org)   
49            Anderson Reporter (andersonreporter.com)   
50     Antelope Valley Today (antelopevalleytoday.com)   
51                        Arab News (www.arabnews.com)   
52           Archaeology World (archaeology-world.com)   
53   Association of American Physicians and Surgeon...   
54                Athens Reporter (athensreporter.com)   
55                      ATL Standard (atlstandard.com)   
56                      Auburn Times (auburntimes.com)   
57                    Backroom Buzz (backroombuzz.com)   
58                    Baldwin Times (baldwintimes.com)   
59           Bare Naked Islam (www.barenakedislam.com)   
60                        Basnews Agency (basnews.com)   
61                                   BB4SP (bb4sp.com)   
62                        Bbarta24 (en.bbarta24.net)\n   
63                                        BDnews24.com   
64       Beach Broadcast News (beachbroadcastnews.com)   
65                        Becker News (beckernews.com)   
66                Before It’s News (beforeitsnews.com)   
67                   Beijing Review (www.bjreview.com)   
68                      Benton Times (bentontime

In [ ]:
news_channel_list.to_csv("News channels.csv", encoding='utf-8', index=False)

In [8]:
news_channels = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/News channels.csv")
news_channels

Name  \
0                                        Accountable.US   
1                                       Act.TV (act.tv)   
2                                           Aftonbladet   
3                                                Al DIA   
4              Alliance for Justice (AFJ) (www.afj.org)   
5                                              Alt News   
6                           Alternet (www.alternet.org)   
7                                 Amandla (aidc.org.za)   
8                        America Blog (americablog.com)   
9     American Bridge 21st Century (americanbridgepa...   
10                                   American Oversight   
11    Americans United for Separation of Church and ...   
12                  Angry White Men (angrywhitemen.org)   
13              Attack the System (attackthesystem.com)   
14                  AutoStraddle (www.autostraddle.com)   
15             Baltimore City Paper (www.citypaper.com)   
16                     Bay Area Reporter (www.ebar.com)   
17                     Being Liberal (www.themaven.net)   
18                    BillMoyers.com (billmoyers.com)\n   
19                         Bitch Media (bitchmedia.org)   
20          Black Agenda Report (blackagendareport.com)   
21              Black America Web (blackamericaweb.com)   
22            Black Lives Matter (blacklivesmatter.com)   
23              Black Main Street (blackmainstreet.net)   
24                          BoingBoing (boingboing.net)   
25                     Boston Review (bostonreview.net)   
26                                           Brut.Media   
27                             Bust Magazine (bust.com)   
28                Call to Activism (calltoactivism.com)   
29               Canada Fact Check (canadafactcheck.ca)   
30           Canadian Dimension (canadiandimension.com)   
31                  Capital & Main (capitalandmain.com)   
32                                Care2 (www.care2.com)   
33         Ceasefire Magazine (ceasefiremagazine.co.uk)   
34    Center for American Progress (www.americanprog...   
35     Center for Media and Democracy (www.prwatch.org)   
36            Center for a Stateless Society (c4ss.org)   
37                 Change.org (https://www.change.org/)   
38               Chicago Reader (www.chicagoreader.com)   
39               Chicago Reporter (chicagoreporter.com)   
40     China Internet Information Center (china.org.cn)   
41                 Citizen Critics (citizencritics.org)   
42            Climate Home News (climatechangenews.com)   
43                                    CNN (www.cnn.com)   
44                         Code Pink (www.codepink.org)   
45                          ColorLines (colorlines.com)   
46    Columbus Free Press (https://columbusfreepress...   
47                                          Comic Sands   
48                 Common Dreams (www.commondreams.org)   
49                    Commune Magazine (communemag.com)   
50                             Cop Block (copblock.org)   
51                  Cosmopolitan (www.cosmopolitan.com)   
52        CounterCurrents.org (www.countercurrents.org)   
53                  CounterPunch (www.counterpunch.org)   
54                               Crikey (crikey.com.au)   
55                          CrimethInc (crimethinc.com)   
56                          Crooked Media (crooked.com)   
57                Crooks and Liars (crooksandliars.com)   
58             Current Affairs (www.currentaffairs.org)   
59                    Curve Magazine (www.curvemag.com)   
60                  Daily Beast (www.thedailybeast.com)   
61                         Daily Dot (www.dailydot.com)   
62                                            Daily Kos   
63                                       Daily News bin   
64      Daily Record (Scotland) (www.dailyrecord.co.uk)   
65         Daily Sound and Fury (dailysoundandfury.com)   
66                   Dallas Voice (www.dallasvoice.com)   
67                            DeadState

In [9]:
news_channels.head()

Name  \
0                            Accountable.US   
1                           Act.TV (act.tv)   
2                               Aftonbladet   
3                                    Al DIA   
4  Alliance for Justice (AFJ) (www.afj.org)   

                                                Link Bias Rating Country  \
0     https://mediabiasfactcheck.com/accountable-us/        left     USA   
1             https://mediabiasfactcheck.com/act-tv/        left     USA   
2        https://mediabiasfactcheck.com/aftonbladet/        left  Sweden   
3             https://mediabiasfactcheck.com/al-dia/        left     USA   
4  https://mediabiasfactcheck.com/alliance-for-ju...        left     USA   

                       Website  
0  https://www.accountable.us/  
1                http://act.tv  
2   https://www.aftonbladet.se  
3        https://aldianews.com  
4         https://www.afj.org/

In [12]:
news_channels[news_channels["Website"] == "https://www.newsmax.com/"]

Name                                     Link  \
2860  Newsmax (www.newsmax.com)  https://mediabiasfactcheck.com/newsmax/   

     Bias Rating Country                   Website  
2860   fake-news     USA  https://www.newsmax.com/

In [19]:
for index, website_links in enumerate(news_channels["Website"][2000:2010]):
    index = news_channels.index[news_channels["Website"] == website_links].tolist()[0]
    print(index, ":", website_links)

2000 : https://www.srnnews.com/
2001 : https://www.sbsun.com
2002 : https://thestarphoenix.com
2003 : https://www.savannahnow.com/
2004 : https://www.scoperatings.com/
2005 : https://sofrep.com/
2006 : https://www.twincities.com/
2007 : https://www.studentnewsdaily.com/
2008 : https://www.tabletmag.com/
2009 : http://www.tallahassee.com/


In [152]:
def find_value(html, key, num_chars=2, separator='"'):
    pos_begin = html.find(key) + len(key) + num_chars
    pos_end = html.find(separator, pos_begin)
    return html[pos_begin: pos_end]

In [36]:
def check_youtube_for_website_link(soup, website_links, twitter_handle_selected):
    domain = get_domain(website_links)
    
    aid = soup.find('script',string=re.compile('ytInitialData')).text
    yt_about_page = json.loads(aid[20:-1])

    #description = yt_about_page['contents']['twoColumnBrowseResultsRenderer']['tabs'][5]['tabRenderer']['content']['sectionListRenderer']['contents'][0]['itemSectionRenderer']['contents'][0]['channelAboutFullMetadataRenderer']['description']['simpleText']

    #youtube_to_website_link = yt_about_page['contents']['twoColumnBrowseResultsRenderer']['tabs'][5]['tabRenderer']['content']['sectionListRenderer']['contents'][0]['itemSectionRenderer']['contents'][0]['channelAboutFullMetadataRenderer']['primaryLinks'][0]['navigationEndpoint']['urlEndpoint']['url']

    #twitter_handle_link = yt_about_page['contents']['twoColumnBrowseResultsRenderer']['tabs'][5]['tabRenderer']['content']['sectionListRenderer']['contents'][0]['itemSectionRenderer']['contents'][0]['channelAboutFullMetadataRenderer']['primaryLinks'][2]['navigationEndpoint']['urlEndpoint']['url']

    # we will use one of them to compare whether the youtube channel we got indeed belongs to that neews channel or not.
    #links_for_checking_authenticity = [youtube_to_website_link, twitter_handle_link]

    links = next(search_dict(yt_about_page, 'primaryLinks'), [])
    links_for_checking_authenticity = []
    for link in links:
        #pp.pprint(link)
        #print("********************")
        #print(link["navigationEndpoint"]["urlEndpoint"]["url"])
        links_for_checking_authenticity.append(link["navigationEndpoint"]["urlEndpoint"]["url"])

    #website_links = "https://aldianews.com"
    #twitter_handle_selected = "ALDIANews"
    for link in links_for_checking_authenticity:
        #print(link)
        redirected_link = parse_qs(unquote(urlparse(link).query))
        #print(redirected_link)
        if 'q' in redirected_link:
            if "http:" in redirected_link['q'][0]:
                redirected_url = get_domain(redirected_link['q'][0])
                #print(redirected_url)
            else:
                redirected_url = re.sub(r'(https?://)?(www.)?', '', redirected_link['q'][0]).split('/', 1)[0]
                #print(redirected_url)

            if "twitter.com" in redirected_link['q'][0]:
                match = re.search(r"^.*?\btwitter\.com/@?([^?/,\r\n]+)(?:[?/,].*)?$", redirected_link['q'][0])                   
                #print(match.group(1))
                if twitter_handle_selected == match.group(1):
                    #print(True)
                    return True
            elif redirected_url == domain:
                #print(True)
                return True
    # can add one more check - domain from description.
    # if we find domain in the description of the youtube about page, then also we can say
    # that we ahve matched the correct youtube channel for that news channel website
    description = next(search_dict(yt_about_page, 'description'), {})
    if len(description) > 0:
        #print(description)
        if domain in description["simpleText"]:
            print("yes, the domain is in the description!")
            return True
    return False

def check_twitter_for_website_link(website_domain, twitter_json):
    """
    To check if the twitter handle we are going to select would belongs to the news channel that we selected during that iteartion.
    website_domain : website that we selected from csv file.
    twitter_json : the html file in json format that we extracted using lookup_users() function.
    
    returns : Boolean
                True: if the twitter handle does belongs to the new channel.
                False: if the twitter handle does NOT belongs to the new channel.
    """
    print("checking ... ")
    if "entities" in twitter_json:
        if "url" in twitter_json["entities"]:
            if "urls" in twitter_json["entities"]["url"]:
                if isinstance(twitter_json["entities"]["url"]["urls"], list):
                    if len(twitter_json["entities"]["url"]["urls"]) > 0:
                        if "expanded_url" in twitter_json["entities"]["url"]["urls"][0]:
                            if twitter_json["entities"]["url"]["urls"][0]["expanded_url"] is not None:  
                                expanded_url = twitter_json["entities"]["url"]["urls"][0]["expanded_url"]
                                if get_domain(website_domain) == get_domain(expanded_url):
                                    if urlparse(get_domain(website_domain)).path == "" or urlparse(get_domain(website_domain)).path == "/":
                                        if urlparse(get_domain(expanded_url)).path == "" or urlparse(get_domain(expanded_url)).path == "/":
                                            print("True")
                                            return True
                                    elif urlparse(get_domain(website_domain)).path.strip("/") == urlparse(get_domain(expanded_url)).path.strip("/"):
                                        print("True")
                                        return True
    print("False")
    return False

def get_domain(url):
    """
    To get th domain form a link
    For eg. http://www.facebook.com -> get_domain("http://www.facebook.com") -> facebook.com
    From github:
    
    """
    return re.sub(r'www\d?.', '', urlparse(url.lower()).netloc.split(':')[0])

In [16]:


num_channels = 0
num_twitter_handle = 0
num_youtube_channels = 0
num_fail_attempts = 0
num_twitter_handle_to_review = 0

twitter_handle_sim_score = defaultdict(float)
new_channel_yt_twitter_sim = pd.DataFrame(columns=['Name', 'Bias Rating', 'Country', 'Website', 'Youtube Channel', 'Twitter Handle', 'Twitter Similarity'])

for index, website_links in enumerate(news_channels["Website"][450:451]):
    new_channel_yt_twitter_sim.loc[index, "Name"] = news_channels["Name"][index]
    new_channel_yt_twitter_sim.loc[index, "Bias Rating"] = news_channels["Bias Rating"][index]
    new_channel_yt_twitter_sim.loc[index, "Country"] = news_channels["Country"][index]
    new_channel_yt_twitter_sim.loc[index, "Website"] = news_channels["Website"][index]
    
    num_channels += 1
    try:
        print("idufghgf")
        twitter_handle = defaultdict(int)
        youtube_channel_id = defaultdict(int)
        youtube_channel_users = defaultdict(int)
        print("{} : {}".format(index, website_links))

        response = requests.get(website_links, headers = headers)
        soup = BeautifulSoup(response.text, 'lxml')

        # trying to find social media link, iei either youtube link or twitter handle.
        website_link = soup.find_all('a', href=True)

        for socialmedia_link in website_link:

            channel_link = socialmedia_link.get("href")

            if "twitter.com" in channel_link.lower():
                    if (bool(re.match(r'https://twitter.com/[\w@]+\??|/?$', channel_link)) and not bool(re.match(r'https://twitter.com/(intent|share|home|hashtag|search)/?', channel_link))
                        and not bool(re.match(r'https://twitter.com/[\w]+/status?', channel_link))):

                        # extract the twitter handle
                        #match = re.search(r'^.*?\btwitter\.com/@?(\w{1,15})(?:[?/,].*)?$', socialmedia_link.get("href").lower())
                        match = re.search(r"^.*?\btwitter\.com/@?([^?/,\r\n]+)(?:[?/,].*)?$", channel_link)                   
                        # increament the dictionary with that key as twiter handle
                        twitter_handle[match.group(1)] += 1
                        print("Twitter handle Dictionary: ", twitter_handle)

            if "youtube.com/" in channel_link:

                if (not(bool(re.match(r'https://www.youtube.com/watch?[\w]+/?', channel_link)))):

                    # it can be channel id or youtube user
                    # Example: 
                    # https://www. youtube.com/channel/UCUZHFZ9jIKrLroW8LcyJEQQ
                    # https://www.youtube.com/channel/UC_WSavcwZVE3ciFM8yCwkBw/
                    # https://www.youtube.com/channel/UCHdWMuH-IIveBWjIsOhK-dw/videos
                    # https://www.youtube.com/channel/UCXu7fg-_KdAoHY7bmahr9vg/featured
                    # https://www.youtube.com/channel/UCmX0gITcFMtmDSah8-wCChw/videos?view_as=subscriber    
                    if (bool(re.match(r'https://www.youtube.com/channel/[\w]+/?', channel_link))):

                        youtube_id = yt_id = re.split(r'/|\?', channel_link)[4]
                        youtube_id = re.split('[^a-zA-Z0-9_-]', youtube_id)[0]
                        print("Youtube Id", youtube_id)
                        youtube_channel_id[youtube_id] += 1

                    # Example: 
                    # https://www.youtube.com/c/AmericanBridgePAC
                    # https://www.youtube.com/c/cosmopolitan?sub_confirmation=1
                    elif (bool(re.match(r'https://www.youtube.com/c/[\w]+/?', channel_link))):
                        youtube_user = re.split(r'/|\?', channel_link)[4]
                        youtube_user = re.split('\W', youtube_user)[0]
                        print("Youtube User", youtube_user)
                        youtube_channel_users[youtube_user] += 1

                    # Example: 
                    # https://www.youtube.com/user/pontealdiatv
                    # https://www.youtube.com/user/blackamericaweb?sub_confirmation=1
                    elif(bool(re.match(r'https://www.youtube.com/user/[\w]+/?', channel_link))):
                        youtube_user = re.split(r'/|\?', channel_link)[4]
                        youtube_user = re.split('\W', youtube_user)[0]
                        print("Youtube User", youtube_user)
                        youtube_channel_users[youtube_user] += 1

                    # Example: https://www.youtube.com/actdottv
                    elif (bool(re.match(r'https://www.youtube.com/[\w]+/?', channel_link))):
                        youtube_user = re.split(r'/|\?', channel_link)[3]
                        youtube_user = re.split('\W', youtube_user)[0]
                        print("Youtube User", youtube_user)
                        youtube_channel_users[youtube_user] += 1

        if(len(twitter_handle)) > 1:
            twitter_handle_list = sorted(list(twitter_handle.keys()), key=lambda x: twitter_handle[x], reverse=True)

            # lookup the user
            try:
                returned_users = api.lookup_users(screen_name=twitter_handle_list)
                for user in returned_users:

                    user_json = user._json
                    screen_name = user_json['screen_name'].lower()
                    print("Screen name: {} / website link: {}  ".format(screen_name, website_links))
                    if check_twitter_for_website_link(website_links, user_json):
                        selected_twitter_handle = screen_name
                        print("Selected twitter handle name: ", selected_twitter_handle)
                        break

            except:
                for twitter_handle in twitter_handle_list:
                    returned_user = api.lookup_users(screen_name = [twitter_handle])[0]

                    user_json = returned_user._json
                    screen_name = user_json['screen_name'].lower()

                    print("Screen name: {} / website link: {}  ".format(screen_name, website_links))           
                    if check_twitter_for_website_link(user_json, website_links):
                        selected_twitter_handle = screen_name
                        print("Selected twitter handle name: ", selected_twitter_handle)
                        break

        elif len(twitter_handle)==1:
            selected_twitter_handle = list(twitter_handle.keys())[0].lower()
            print("Twitter with only on handle: ", selected_twitter_handle)

        if selected_twitter_handle != '':
            num_twitter_handle += 1
            print("website domain name: ", tldextract.extract(get_domain(website_links)).domain)
            tw_similarity = SequenceMatcher(None, tldextract.extract(get_domain(website_links)).domain, selected_twitter_handle).ratio()

            new_channel_yt_twitter_sim.loc[index, "Twitter Handle"] = selected_twitter_handle
            new_channel_yt_twitter_sim.loc[index, "Twitter Similarity"] = tw_similarity
            
            # twitter handle to be reviewed
            twitter_handle_sim_score[selected_twitter_handle] = tw_similarity
            
            print("similarity: ", tw_similarity)
            selected_twitter_handle = ""

        # if we extracted more than one youtube id for a single new channel, we
        # need to select from one of them
        print("Youtube channel Id Dictionary", youtube_channel_id)
        headers= {"User-Agent": "Mozilla/5.0 (compatible; Googlebot/2.1; +http://www.google.com/bot.html)"}

        select_youtube_id = ""
        if(len(youtube_channel_id) > 1):
            youtube_id_list = sorted(list(youtube_channel_id.keys()), key=lambda x: youtube_channel_id[x], reverse=True)
            print(youtube_id_list)
            for ids in youtube_id_list:
                print("Youtube Channel link : https://www.youtube.com/channel/{}/about".format(ids))
                yt_about_page = requests.get("https://www.youtube.com/channel/{}/about".format(ids), headers=headers)
                soup = BeautifulSoup(yt_about_page.content, features='html.parser')

                if check_youtube_for_website_link(soup, website_links, selected_twitter_handle):
                    select_youtube_id = ids
                    break
        elif len(youtube_channel_id) == 1:
            select_youtube_id = list(youtube_channel_id.keys())[0]
        print("selected youtube id: ", select_youtube_id)

        if select_youtube_id != "":
            new_channel_yt_twitter_sim.loc[index, "Youtube Channel"] = select_youtube_id
        
        # Test the above code and write code for select_youtube_user
        print("Youtube channel User Dictionary", youtube_channel_users)

        select_youtube_user = ""
        if (len(youtube_channel_users) > 1):
            youtube_user_list = sorted(list(youtube_channel_users.keys()), key=lambda x: youtube_channel_users[x], reverse=True)
            print(youtube_user_list)
            for users in youtube_user_list:
                print("Youtube Channel link : https://www.youtube.com/channel/{}/about".format(users))
                yt_about_page = requests.get("https://www.youtube.com/channel/{}/about".format(users), headers=headers)
                soup = BeautifulSoup(yt_about_page.content, features='html.parser')

                if check_youtube_for_website_link(soup, website_links, selected_twitter_handle):
                    select_youtube_user = users
                    break
        elif len(youtube_channel_users) == 1:
            select_youtube_user = list(youtube_channel_users.keys())[0]
        print("selected youtube user: ", select_youtube_user)

        if select_youtube_user != "":
            new_channel_yt_twitter_sim.loc[index, "Youtube Channel"] = select_youtube_user
        
        # statistics:
        if select_youtube_id != "" or select_youtube_user != "":
            num_youtube_channels += 1
        print("***************************************")
    except:
        num_fail_attempts += 1
        continue


for selected_twitter_handle, tw_similarity in twitter_handle_sim_score.items():           
    if isinstance(tw_similarity, float) and tw_similarity < 0.5:
        num_twitter_handle_to_review += 1
        print("Twitter handles to be reviewed: {} with Similarity: ".format(selected_twitter_handle, tw_similarity))

print("Number of twitter handle found/Number of total News channels : {} / {}".format(num_twitter_handle, num_channels))
print("Number of youtube user/id found/Number of total News channels : {} / {}".format(num_youtube_channels, num_channels))
print("Number of failed attempts/Total attempts or News channels : {} / {}".format(num_fail_attempts, num_channels))
print("Number of twitter to be reviewed: {}".format(num_twitter_handle_to_review))

idufghgf
0 : https://www.charlotteobserver.com
Number of twitter handle found/Number of total News channels : 0 / 1
Number of youtube user/id found/Number of total News channels : 0 / 1
Number of failed attempts/Total attempts or News channels : 1 / 1
Number of twitter to be reviewed: 0


In [65]:
twitter_handle

defaultdict(int,
            {'accountable_us': 3,
             'actdottv': 1,
             'aldianews': 2,
             'afjustice': 3,
             'altnews': 2,
             'AlterNet': 2,
             'alternet': 1,
             'AmandlaMedia': 7,
             'SAHRCommission': 1,
             'American_Bridge': 3,
             'americansunited': 1,
             'autostraddle': 2,
             'BeingLiberal': 1,
             'BillMoyers': 1,
             'bitchmedia': 2,
             'blkagendareport': 1,
             'BJSocialNetwork': 2,
             'frauenfelder': 1,
             'pesco': 1,
             'beschizza': 1,
             'carla_sinclair': 1,
             'jlw': 1,
             'orenwolf': 1,
             'BostonReview': 6,
             'bust_magazine': 1,
             'jegtheme': 1,
             'CDN_Dimension': 1,
             'capitalandmain': 3,
             'Care2': 1,
             'CeasefireMag': 1,
             'amprog': 1,
             'exposedbycmd': 1,
    

To get twitter handle, get several types of twitter links, thet are as follows:
1. https://twitter.com/accountable_us?ref_src=twsrc%5Etfw
2. https://twitter.com/accountable_us
3. https://twitter.com/@American_Bridge
4. https://twitter.com/intent/tweet?in_reply_to=1524776220386283522  ignore this one
5. https://twitter.com/intent/retweet?tweet_id=1524776220386283522  ignore this one
6. https://twitter.com/intent/like?tweet_id=1524776220386283522  ignore this one
7. https://twitter.com/search?q=%23EndTheBookFamine   ignore this one

To get youtube channel name, we got following links: <Br>
    1. https://www.youtube.com/watch?v=QPgPteVrl3s - ignore this one <Br>
    2. www.youtube.com/embed/m2LdbBgyOlQ - ignore this one <Br>
    3. https://www.youtube.com/actdottv <Br>
    4. https://www.youtube.com/user/pontealdiatv <Br>
    5. https://www.youtube.com/user/blackamericaweb?sub_confirmation=1 <Br>
    <Br>
    6. https://www.youtube.com/channel/UCmX0gITcFMtmDSah8-wCChw/videos?view_as=subscriber <Br>
    7. https://www.youtube.com/channel/UC_WSavcwZVE3ciFM8yCwkBw/ <Br>
    8. https://www.youtube.com/channel/UCjfpIrbyc1hMT-CRZWbGF4g <Br>
    9. https://www.youtube.com/c/AmericanBridgePAC <Br>
    10. https://www.youtube.com/c/cosmopolitan?sub_confirmation=1 <Br>
    11. https://www.youtube.com/channel/UCXu7fg-_KdAoHY7bmahr9vg/featured <Br>
    12. https://www.youtube.com/channel/UCHdWMuH-IIveBWjIsOhK-dw/videos <Br>

In [ ]:
# some original, 2.1 from ours.

In [13]:
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/2. scrap_youtube_twitter.csv")
channel_yt_twitter

Name   Bias Rating  \
0                                        Accountable.US          left   
1                                       Act.TV (act.tv)          left   
2                                           Aftonbladet          left   
3                                                Al DIA          left   
4              Alliance for Justice (AFJ) (www.afj.org)          left   
5                                              Alt News          left   
6                           Alternet (www.alternet.org)          left   
7                                 Amandla (aidc.org.za)          left   
8                        America Blog (americablog.com)          left   
9     American Bridge 21st Century (americanbridgepa...          left   
10                                   American Oversight          left   
11    Americans United for Separation of Church and ...          left   
12                  Angry White Men (angrywhitemen.org)          left   
13              Attack the System (attackthesystem.com)          left   
14                  AutoStraddle (www.autostraddle.com)          left   
15             Baltimore City Paper (www.citypaper.com)          left   
16                     Bay Area Reporter (www.ebar.com)          left   
17                     Being Liberal (www.themaven.net)          left   
18                    BillMoyers.com (billmoyers.com)\n          left   
19                         Bitch Media (bitchmedia.org)          left   
20          Black Agenda Report (blackagendareport.com)          left   
21              Black America Web (blackamericaweb.com)          left   
22            Black Lives Matter (blacklivesmatter.com)          left   
23              Black Main Street (blackmainstreet.net)          left   
24                          BoingBoing (boingboing.net)          left   
25                     Boston Review (bostonreview.net)          left   
26                                           Brut.Media          left   
27                             Bust Magazine (bust.com)          left   
28                Call to Activism (calltoactivism.com)          left   
29               Canada Fact Check (canadafactcheck.ca)          left   
30           Canadian Dimension (canadiandimension.com)          left   
31                  Capital & Main (capitalandmain.com)          left   
32                                Care2 (www.care2.com)          left   
33         Ceasefire Magazine (ceasefiremagazine.co.uk)          left   
34    Center for American Progress (www.americanprog...          left   
35     Center for Media and Democracy (www.prwatch.org)          left   
36            Center for a Stateless Society (c4ss.org)          left   
37                 Change.org (https://www.change.org/)          left   
38               Chicago Reader (www.chicagoreader.com)          left   
39               Chicago Reporter (chicagoreporter.com)          left   
40     China Internet Information Center (china.org.cn)          left   
41                 Citizen Critics (citizencritics.org)          left   
42            Climate Home News (climatechangenews.com)          left   
43                                    CNN (www.cnn.com)          left   
44                         Code Pink (www.codepink.org)          left   
45                          ColorLines (colorlines.com)          left   
46    Columbus Free Press (https://columbusfreepress...          left   
47                                          Comic Sands          left   
48                 Common Dreams (www.commondreams.org)          left   
49                    Commune Magazine (communemag.com)          left   
50                             Cop Block (copblock.org)          left   
51                  Cosmopolitan (www.cosmopolitan.com)          left   
52        CounterCurrents.org (www.countercurrents.org)          left   
53                  CounterPunch (www.counterpunch.org)          left   
54                               Cri

In [46]:
update_twitter = channel_yt_twitter[channel_yt_twitter["Twitter Similarity"] < 0.5]

In [47]:
update_twitter

Name   Bias Rating  \
23              Black Main Street (blackmainstreet.net)          left   
27                             Bust Magazine (bust.com)          left   
29               Canada Fact Check (canadafactcheck.ca)          left   
35     Center for Media and Democracy (www.prwatch.org)          left   
75         Deshabhimani (https://www.deshabhimani.com/)          left   
79                       Drudge Retort (www.drudge.com)          left   
83          Electoral-Vote.com (www.electoral-vote.com)          left   
93                   Fifth Estate (www.fifthestate.org)          left   
112                            GQ Magazine (www.gq.com)          left   
120                    Hill Reporter (hillreporter.com)          left   
127     Informed Comment (Juan Cole) (www.juancole.com)          left   
134                  It’s Going Down (itsgoingdown.org)          left   
152                    Media Matters (mediamatters.org)          left   
160    Milwaukee Independent (milwaukeeindependent.org)          left   
161                Modern Liberals (modernliberals.com)          left   
199                  Popular Information (popular.info)          left   
247         The Burning Spear (www.theburningspear.com)          left   
257              The Dworkin Report (dworkinreport.com)          left   
265         The Intellectualist (theintellectualist.co)          left   
298                Unicorn Riot (www.unicornriot.ninja)          left   
300                         Upworthy (www.upworthy.com)          left   
311             White House Watch (whitehousewatch.com)          left   
313                             Wonkette (wonkette.com)          left   
323                           ABC News (abcnews.go.com)   center-left   
324                 ABC News Australia (www.abc.net.au)   center-left   
336                      Al Jazeera (www.aljazeera.com)   center-left   
367     Asheville Citizen-Times (www.citizen-times.com)   center-left   
399          Bluestem Prairie (www.bluestemprairie.com)   center-left   
466                             Daily Hampshire Gazette   center-left   
478                  Democracy 21 (www.democracy21.org)   center-left   
479   Democrat and Chronicle (www.democratandchronic...   center-left   
494             Economic Policy Institute (www.epi.org)   center-left   
541   Government Accountability Project (whistleblow...   center-left   
558                     High Country News (www.hcn.org)   center-left   
560            Hindustan Times (www.hindustantimes.com)   center-left   
561       History News Network (historynewsnetwork.org)   center-left   
562      Hollywood Reporter (www.hollywoodreporter.com)   center-left   
574                                 iNews (inews.co.uk)   center-left   
601          KCNC-TV – CBS Denver (denver.cbslocal.com)   center-left   
606     KOVR – CBS Sacramento (sacramento.cbslocal.com)   center-left   
664          Naked Capitalism (www.nakedcapitalism.com)   center-left   
671   Natural Resource Governance Institute (www.res...   center-left   
709               Pacific Standard Magazine (psmag.com)   center-left   
714                         PBS News Hour (www.pbs.org)   center-left   
743                       Radio Free Asia (www.rfa.org)   center-left   
744   Radio Television Marti (radiotelevisionmarti.com)   center-left   
748            Religion News Service (religionnews.com)   center-left   
752              Richmond Palladium-Item (pal-item.com)   center-left   
782           Springfield News-Leader (news-leader.com)   center-left   
786                            Star Ledger (www.nj.com)   center-left   
806                               The Asbury Park Press   center-left   
836            The Herald (Everett) (www.heraldnet.com)   center-left   
855                          The Motley Fool (fool.com)   center-left   
865          The Press Democrat (www.pressdemocrat.com)   center-left   
921         Visalia Times-Delta (vis

In [48]:
update_twitter.loc[27, "Twitter Handle"] = ""

C:\Users\wasil\Anaconda3\lib\site-packages\pandas\core\indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


In [49]:
update_twitter

Name   Bias Rating  \
23              Black Main Street (blackmainstreet.net)          left   
27                             Bust Magazine (bust.com)          left   
29               Canada Fact Check (canadafactcheck.ca)          left   
35     Center for Media and Democracy (www.prwatch.org)          left   
75         Deshabhimani (https://www.deshabhimani.com/)          left   
79                       Drudge Retort (www.drudge.com)          left   
83          Electoral-Vote.com (www.electoral-vote.com)          left   
93                   Fifth Estate (www.fifthestate.org)          left   
112                            GQ Magazine (www.gq.com)          left   
120                    Hill Reporter (hillreporter.com)          left   
127     Informed Comment (Juan Cole) (www.juancole.com)          left   
134                  It’s Going Down (itsgoingdown.org)          left   
152                    Media Matters (mediamatters.org)          left   
160    Milwaukee Independent (milwaukeeindependent.org)          left   
161                Modern Liberals (modernliberals.com)          left   
199                  Popular Information (popular.info)          left   
247         The Burning Spear (www.theburningspear.com)          left   
257              The Dworkin Report (dworkinreport.com)          left   
265         The Intellectualist (theintellectualist.co)          left   
298                Unicorn Riot (www.unicornriot.ninja)          left   
300                         Upworthy (www.upworthy.com)          left   
311             White House Watch (whitehousewatch.com)          left   
313                             Wonkette (wonkette.com)          left   
323                           ABC News (abcnews.go.com)   center-left   
324                 ABC News Australia (www.abc.net.au)   center-left   
336                      Al Jazeera (www.aljazeera.com)   center-left   
367     Asheville Citizen-Times (www.citizen-times.com)   center-left   
399          Bluestem Prairie (www.bluestemprairie.com)   center-left   
466                             Daily Hampshire Gazette   center-left   
478                  Democracy 21 (www.democracy21.org)   center-left   
479   Democrat and Chronicle (www.democratandchronic...   center-left   
494             Economic Policy Institute (www.epi.org)   center-left   
541   Government Accountability Project (whistleblow...   center-left   
558                     High Country News (www.hcn.org)   center-left   
560            Hindustan Times (www.hindustantimes.com)   center-left   
561       History News Network (historynewsnetwork.org)   center-left   
562      Hollywood Reporter (www.hollywoodreporter.com)   center-left   
574                                 iNews (inews.co.uk)   center-left   
601          KCNC-TV – CBS Denver (denver.cbslocal.com)   center-left   
606     KOVR – CBS Sacramento (sacramento.cbslocal.com)   center-left   
664          Naked Capitalism (www.nakedcapitalism.com)   center-left   
671   Natural Resource Governance Institute (www.res...   center-left   
709               Pacific Standard Magazine (psmag.com)   center-left   
714                         PBS News Hour (www.pbs.org)   center-left   
743                       Radio Free Asia (www.rfa.org)   center-left   
744   Radio Television Marti (radiotelevisionmarti.com)   center-left   
748            Religion News Service (religionnews.com)   center-left   
752              Richmond Palladium-Item (pal-item.com)   center-left   
782           Springfield News-Leader (news-leader.com)   center-left   
786                            Star Ledger (www.nj.com)   center-left   
806                               The Asbury Park Press   center-left   
836            The Herald (Everett) (www.heraldnet.com)   center-left   
855                          The Motley Fool (fool.com)   center-left   
865          The Press Democrat (www.pressdemocrat.com)   center-left   
921         Visalia Times-Delta (vis

In [9]:
# 4th one from original, 3rd for ourself

In [58]:
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/2. scrap_youtube_twitter.csv")
channel_yt_twitter

Name  Bias Rating  \
0                                       Accountable.US         left   
1                                      Act.TV (act.tv)         left   
2                                          Aftonbladet         left   
3                                               Al DIA         left   
4             Alliance for Justice (AFJ) (www.afj.org)         left   
5                                             Alt News         left   
6                          Alternet (www.alternet.org)         left   
7                                Amandla (aidc.org.za)         left   
8                       America Blog (americablog.com)         left   
9    American Bridge 21st Century (americanbridgepa...         left   
10                                  American Oversight         left   
11   Americans United for Separation of Church and ...         left   
12                 Angry White Men (angrywhitemen.org)         left   
13             Attack the System (attackthesystem.com)         left   
14                 AutoStraddle (www.autostraddle.com)         left   
15            Baltimore City Paper (www.citypaper.com)         left   
16                    Bay Area Reporter (www.ebar.com)         left   
17                    Being Liberal (www.themaven.net)         left   
18                   BillMoyers.com (billmoyers.com)\n         left   
19                        Bitch Media (bitchmedia.org)         left   
20         Black Agenda Report (blackagendareport.com)         left   
21             Black America Web (blackamericaweb.com)         left   
22           Black Lives Matter (blacklivesmatter.com)         left   
23             Black Main Street (blackmainstreet.net)         left   
24                         BoingBoing (boingboing.net)         left   
25                    Boston Review (bostonreview.net)         left   
26                                          Brut.Media         left   
27                            Bust Magazine (bust.com)         left   
28               Call to Activism (calltoactivism.com)         left   
29              Canada Fact Check (canadafactcheck.ca)         left   
30          Canadian Dimension (canadiandimension.com)         left   
31                 Capital & Main (capitalandmain.com)         left   
32                               Care2 (www.care2.com)         left   
33        Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34   Center for American Progress (www.americanprog...         left   
35    Center for Media and Democracy (www.prwatch.org)         left   
36           Center for a Stateless Society (c4ss.org)         left   
37                Change.org (https://www.change.org/)         left   
38              Chicago Reader (www.chicagoreader.com)         left   
39              Chicago Reporter (chicagoreporter.com)         left   
40    China Internet Information Center (china.org.cn)         left   
41                Citizen Critics (citizencritics.org)         left   
42           Climate Home News (climatechangenews.com)         left   
43                                   CNN (www.cnn.com)         left   
44                        Code Pink (www.codepink.org)         left   
45                         ColorLines (colorlines.com)         left   
46   Columbus Free Press (https://columbusfreepress...         left   
47                                         Comic Sands         left   
48                Common Dreams (www.commondreams.org)         left   
49                   Commune Magazine (communemag.com)         left   
50                            Cop Block (copblock.org)         left   
51                 Cosmopolitan (www.cosmopolitan.com)         left   
52       CounterCurrents.org (www.countercurrents.org)         left   
53                 CounterPunch (www.counterpunch.org)         left   
54                              Crikey (crikey.com.au)         left   
55                         CrimethInc (crimethinc.com)         left   
56 

In [59]:
channel_yt_twitter = channel_yt_twitter.reset_index()

In [60]:
update_csv = False

# statistics
num_requests_sent = 0
num_updates = 0
num_fail_attempts = 0

for index, row in channel_yt_twitter.iterrows():

    if pd.isna(channel_yt_twitter.iloc[index, 6]):
        channel_name = channel_yt_twitter.iloc[index, 1]
        website_links = channel_yt_twitter.iloc[index, 4]
        
        returned_users = api.search_users(channel_name, count = 10)
        num_requests_sent += 1
        update_csv = True
        
        for user in returned_users:
            user_json = user._json
            screen_name = user_json['screen_name'].lower()
            print("Screen name: {} / website link: {}  ".format(screen_name, website_links))
            
            if not pd.isna(website_links):
                if check_twitter_for_website_link(website_links, user_json):

                    selected_twitter_handle = screen_name
                    print("Selected twitter handle name: ", selected_twitter_handle)

                    tw_similarity = SequenceMatcher(None, tldextract.extract(get_domain(website_links)).domain, selected_twitter_handle).ratio()
                    print(tw_similarity)

                    channel_yt_twitter.iloc[index, 6] = selected_twitter_handle
                    channel_yt_twitter.iloc[index, 7] = tw_similarity
                    num_updates += 1
                    update_csv = False
                    break
        if update_csv == True:
            num_fail_attempts += 1
            update_csv = False
            
print("Number of successfull update {} / Number of requests sent: {}".format(num_updates, num_requests_sent))
print("Number of Failed update {} / Number of requests sent: {}".format(num_fail_attempts, num_requests_sent))

Screen name: aftonbladet / website link: https://www.aftonbladet.se  
checking ... 
True
Selected twitter handle name:  aftonbladet
1.0
Screen name: weareoversight / website link: https://www.americanoversight.org  
checking ... 
True
Selected twitter handle name:  weareoversight
0.7096774193548387
Screen name: blackamericaweb / website link: https://blackamericaweb.com/  
checking ... 
True
Selected twitter handle name:  blackamericaweb
1.0
Screen name: boingboing / website link: https://boingboing.net  
checking ... 
True
Selected twitter handle name:  boingboing
1.0
Screen name: ukchange / website link: https://www.change.org/  
checking ... 
True
Selected twitter handle name:  ukchange
0.8571428571428571
Screen name: chinaorgcn / website link: http://www.china.org.cn/  
checking ... 
True
Selected twitter handle name:  chinaorgcn
0.6666666666666666
Screen name: httpcnn / website link: https://www.cnn.com/  
checking ... 
False
Screen name: blalkjalskdjfas / website link: https://ww

In [43]:
channel_yt_twitter

index                                               Name  Bias Rating  \
0        0                                     Accountable.US         left   
1        1                                    Act.TV (act.tv)         left   
2        2                                        Aftonbladet         left   
3        3                                             Al DIA         left   
4        4           Alliance for Justice (AFJ) (www.afj.org)         left   
5        5                                           Alt News         left   
6        6                        Alternet (www.alternet.org)         left   
7        7                              Amandla (aidc.org.za)         left   
8        8                     America Blog (americablog.com)         left   
9        9  American Bridge 21st Century (americanbridgepa...         left   
10      10                                 American Oversight         left   
11      11  Americans United for Separation of Church and ...         left   
12      12                Angry White Men (angrywhitemen.org)         left   
13      13            Attack the System (attackthesystem.com)         left   
14      14                AutoStraddle (www.autostraddle.com)         left   
15      15           Baltimore City Paper (www.citypaper.com)         left   
16      16                   Bay Area Reporter (www.ebar.com)         left   
17      17                   Being Liberal (www.themaven.net)         left   
18      18                  BillMoyers.com (billmoyers.com)\n         left   
19      19                       Bitch Media (bitchmedia.org)         left   
20      20        Black Agenda Report (blackagendareport.com)         left   
21      21            Black America Web (blackamericaweb.com)         left   
22      22          Black Lives Matter (blacklivesmatter.com)         left   
23      23            Black Main Street (blackmainstreet.net)         left   
24      24                        BoingBoing (boingboing.net)         left   
25      25                   Boston Review (bostonreview.net)         left   
26      26                                         Brut.Media         left   
27      27                           Bust Magazine (bust.com)         left   
28      28              Call to Activism (calltoactivism.com)         left   
29      29             Canada Fact Check (canadafactcheck.ca)         left   
30      30         Canadian Dimension (canadiandimension.com)         left   
31      31                Capital & Main (capitalandmain.com)         left   
32      32                              Care2 (www.care2.com)         left   
33      33       Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34      34  Center for American Progress (www.americanprog...         left   
35      35   Center for Media and Democracy (www.prwatch.org)         left   
36      36          Center for a Stateless Society (c4ss.org)         left   
37      37               Change.org (https://www.change.org/)         left   
38      38             Chicago Reader (www.chicagoreader.com)         left   
39      39             Chicago Reporter (chicagoreporter.com)         left   
40      40   China Internet Information Center (china.org.cn)         left   
41      41               Citizen Critics (citizencritics.org)         left   
42      42          Climate Home News (climatechangenews.com)         left   
43      43                                  CNN (www.cnn.com)         left   
44      44                       Code Pink (www.codepink.org)         left   
45      45                        ColorLines (colorlines.com)         left   
46      46  Columbus Free Press (https://columbusfreepress...         left   
47      47                                        Comic Sands         left   
48      48               Common Dreams (www.commondreams.org)         left   
49      49                  Commune Magazine (communemag.com)         left   
50      50                 

In [7]:
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/3. scrap_youtube_twitter_handle.csv")
channel_yt_twitter

index                                               Name  Bias Rating  \
0        0                                     Accountable.US         left   
1        1                                    Act.TV (act.tv)         left   
2        2                                        Aftonbladet         left   
3        3                                             Al DIA         left   
4        4           Alliance for Justice (AFJ) (www.afj.org)         left   
5        5                                           Alt News         left   
6        6                        Alternet (www.alternet.org)         left   
7        7                              Amandla (aidc.org.za)         left   
8        8                     America Blog (americablog.com)         left   
9        9  American Bridge 21st Century (americanbridgepa...         left   
10      10                                 American Oversight         left   
11      11  Americans United for Separation of Church and ...         left   
12      12                Angry White Men (angrywhitemen.org)         left   
13      13            Attack the System (attackthesystem.com)         left   
14      14                AutoStraddle (www.autostraddle.com)         left   
15      15           Baltimore City Paper (www.citypaper.com)         left   
16      16                   Bay Area Reporter (www.ebar.com)         left   
17      17                   Being Liberal (www.themaven.net)         left   
18      18                  BillMoyers.com (billmoyers.com)\n         left   
19      19                       Bitch Media (bitchmedia.org)         left   
20      20        Black Agenda Report (blackagendareport.com)         left   
21      21            Black America Web (blackamericaweb.com)         left   
22      22          Black Lives Matter (blacklivesmatter.com)         left   
23      23            Black Main Street (blackmainstreet.net)         left   
24      24                        BoingBoing (boingboing.net)         left   
25      25                   Boston Review (bostonreview.net)         left   
26      26                                         Brut.Media         left   
27      27                           Bust Magazine (bust.com)         left   
28      28              Call to Activism (calltoactivism.com)         left   
29      29             Canada Fact Check (canadafactcheck.ca)         left   
30      30         Canadian Dimension (canadiandimension.com)         left   
31      31                Capital & Main (capitalandmain.com)         left   
32      32                              Care2 (www.care2.com)         left   
33      33       Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34      34  Center for American Progress (www.americanprog...         left   
35      35   Center for Media and Democracy (www.prwatch.org)         left   
36      36          Center for a Stateless Society (c4ss.org)         left   
37      37               Change.org (https://www.change.org/)         left   
38      38             Chicago Reader (www.chicagoreader.com)         left   
39      39             Chicago Reporter (chicagoreporter.com)         left   
40      40   China Internet Information Center (china.org.cn)         left   
41      41               Citizen Critics (citizencritics.org)         left   
42      42          Climate Home News (climatechangenews.com)         left   
43      43                                  CNN (www.cnn.com)         left   
44      44                       Code Pink (www.codepink.org)         left   
45      45                        ColorLines (colorlines.com)         left   
46      46  Columbus Free Press (https://columbusfreepress...         left   
47      47                                        Comic Sands         left   
48      48               Common Dreams (www.commondreams.org)         left   
49      49                  Commune Magazine (communemag.com)         left   
50      50                 

In [8]:
# 5 form the original and 4th for ours.

In [57]:
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/3. scrap_youtube_twitter_handle.csv")
channel_yt_twitter.drop("index",axis=1,inplace=True)
channel_yt_twitter

Name  Bias Rating  \
0                                       Accountable.US         left   
1                                      Act.TV (act.tv)         left   
2                                          Aftonbladet         left   
3                                               Al DIA         left   
4             Alliance for Justice (AFJ) (www.afj.org)         left   
5                                             Alt News         left   
6                          Alternet (www.alternet.org)         left   
7                                Amandla (aidc.org.za)         left   
8                       America Blog (americablog.com)         left   
9    American Bridge 21st Century (americanbridgepa...         left   
10                                  American Oversight         left   
11   Americans United for Separation of Church and ...         left   
12                 Angry White Men (angrywhitemen.org)         left   
13             Attack the System (attackthesystem.com)         left   
14                 AutoStraddle (www.autostraddle.com)         left   
15            Baltimore City Paper (www.citypaper.com)         left   
16                    Bay Area Reporter (www.ebar.com)         left   
17                    Being Liberal (www.themaven.net)         left   
18                   BillMoyers.com (billmoyers.com)\n         left   
19                        Bitch Media (bitchmedia.org)         left   
20         Black Agenda Report (blackagendareport.com)         left   
21             Black America Web (blackamericaweb.com)         left   
22           Black Lives Matter (blacklivesmatter.com)         left   
23             Black Main Street (blackmainstreet.net)         left   
24                         BoingBoing (boingboing.net)         left   
25                    Boston Review (bostonreview.net)         left   
26                                          Brut.Media         left   
27                            Bust Magazine (bust.com)         left   
28               Call to Activism (calltoactivism.com)         left   
29              Canada Fact Check (canadafactcheck.ca)         left   
30          Canadian Dimension (canadiandimension.com)         left   
31                 Capital & Main (capitalandmain.com)         left   
32                               Care2 (www.care2.com)         left   
33        Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34   Center for American Progress (www.americanprog...         left   
35    Center for Media and Democracy (www.prwatch.org)         left   
36           Center for a Stateless Society (c4ss.org)         left   
37                Change.org (https://www.change.org/)         left   
38              Chicago Reader (www.chicagoreader.com)         left   
39              Chicago Reporter (chicagoreporter.com)         left   
40    China Internet Information Center (china.org.cn)         left   
41                Citizen Critics (citizencritics.org)         left   
42           Climate Home News (climatechangenews.com)         left   
43                                   CNN (www.cnn.com)         left   
44                        Code Pink (www.codepink.org)         left   
45                         ColorLines (colorlines.com)         left   
46   Columbus Free Press (https://columbusfreepress...         left   
47                                         Comic Sands         left   
48                Common Dreams (www.commondreams.org)         left   
49                   Commune Magazine (communemag.com)         left   
50                            Cop Block (copblock.org)         left   
51                 Cosmopolitan (www.cosmopolitan.com)         left   
52       CounterCurrents.org (www.countercurrents.org)         left   
53                 CounterPunch (www.counterpunch.org)         left   
54                              Crikey (crikey.com.au)         left   
55                         CrimethInc (crimethinc.com)         left   
56 

In [53]:
def youtube_search_bar(channel_name):
    r = "https://www.youtube.com/results?search_query={}".format(channel_name)
    return r

In [58]:
for index, row in channel_yt_twitter.iterrows():
    
    
    num_search_results = 0
    
    # if we dont have channel name or its user id
    if pd.isna(channel_yt_twitter.iloc[index, 4]):
        print("*********************")
        print("Channel name: ", channel_yt_twitter.iloc[index, 0])
        for _ in range(5):
            if num_search_results == 0:
                result_link = youtube_search_bar(channel_yt_twitter.iloc[index, 0])
                try:
                    response = requests.get(result_link, headers = headers)
                except:
                    response = requests.get(result_link)
                time.sleep(1)

                if response.text:
                    soup = BeautifulSoup(response.text, 'lxml')

                    #print(soup)

                    aid = soup.find('script',string=re.compile('ytInitialData')).text
                    yt_about_page = json.loads(aid[20:-1])
                    
                    #pp.pprint(yt_about_page)

                    result_lists = yt_about_page["contents"]["twoColumnSearchResultsRenderer"]["primaryContents"] \
                       ["sectionListRenderer"]["contents"][0]["itemSectionRenderer"]["contents"]

                    #result_list = recursive_lookup("channelRenderer", yt_about_page)
                    list_of_retrieved_channel_json = []
                    for r in result_lists:
                        
                        if list(r.keys())[0] == "channelRenderer":
                            print("channel result found on the seach result")
                            list_of_retrieved_channel_json.append(r)
                            num_search_results = len(list_of_retrieved_channel_json)
    

*********************
Channel name:  Accountable.US
channel result found on the seach result
*********************
Channel name:  Aftonbladet
channel result found on the seach result
*********************
Channel name:  Alternet (www.alternet.org)
channel result found on the seach result
channel result found on the seach result
*********************
Channel name:  America Blog (americablog.com)
*********************
Channel name:  American Oversight
*********************
Channel name:  Americans United for Separation of Church and State (www.au.org)
*********************
Channel name:  Angry White Men (angrywhitemen.org)
*********************
Channel name:  Attack the System (attackthesystem.com)
channel result found on the seach result
*********************
Channel name:  AutoStraddle (www.autostraddle.com)
channel result found on the seach result
*********************
Channel name:  Baltimore City Paper (www.citypaper.com)
channel result found on the seach result
********************

KeyboardInterrupt: 

In [74]:
website_name = "Climate Home News (climatechangenews.com)"

def get_website_name(website_name):
    if "(" in website_name:
        print(website_name)
        print(website_name.split("(", 1))
        splitted_list = website_name.split("(", 1)
        for sl in splitted_list:
            if (")" not in sl) and ("(" not in sl):
                if ".com" not in sl:
                    print(sl.strip())
                    return sl.strip()
    

In [75]:
for index, row in channel_yt_twitter.iterrows():
    
    num_search_results = 0
    
    # if we dont have channel name or its user id
    if pd.isna(channel_yt_twitter.iloc[index, 4]):
        print("*********************")
        print("Channel name: ", channel_yt_twitter.iloc[index, 0])
        for _ in range(5):
            if num_search_results == 0:
                result_link = youtube_search_bar(channel_yt_twitter.iloc[index, 0])
                try:
                    response = requests.get(result_link, headers = headers)
                except:
                    response = requests.get(result_link)
                time.sleep(1)

                if response.text:
                    soup = BeautifulSoup(response.text, 'lxml')

                    #print(soup)

                    aid = soup.find('script',string=re.compile('ytInitialData')).text
                    yt_about_page = json.loads(aid[20:-1])
                    
                    #pp.pprint(yt_about_page)

                    result_lists = yt_about_page["contents"]["twoColumnSearchResultsRenderer"]["primaryContents"] \
                       ["sectionListRenderer"]["contents"][0]["itemSectionRenderer"]["contents"]

                    #result_list = recursive_lookup("channelRenderer", yt_about_page)
                    list_of_retrieved_channel_json = []
                    for r in result_lists:
                        
                        if list(r.keys())[0] == "channelRenderer":
                            print("channel result found on the seach result")
                            list_of_retrieved_channel_json.append(r)
                            num_search_results = len(list_of_retrieved_channel_json)
        
        
        for channel_json in list_of_retrieved_channel_json:    
            channel_id = channel_json["channelRenderer"]["channelId"]
            channel_title = channel_json["channelRenderer"]["title"]["simpleText"]
            print(channel_id, channel_title)
            
            # check if we got the right youtube channel or not.
            # we can compare it with the domain of the website and twitter handle.
            header = {"User-Agent": "Mozilla/5.0 (compatible; Googlebot/2.1; +http://www.google.com/bot.html)"}
            if channel_title != "":
                about_page = "https://www.youtube.com/channel/{}/about".format(channel_id)
                yt_about_page = requests.get(about_page, headers=header)
                time.sleep(1)
                soup = BeautifulSoup(yt_about_page.content, features='html.parser')
                
                if check_youtube_for_website_link(soup, channel_yt_twitter.iloc[index, 3], channel_yt_twitter.iloc[index, 5]):
                    print("match found!")
                    # update the csv file.
                    channel_yt_twitter.iloc[index, 4] = channel_title
        
        

*********************
Channel name:  Accountable.US
channel result found on the seach result
UCRvUQd-GsCR97qKReTE89jQ Accountable US
match found!
*********************
Channel name:  Aftonbladet
channel result found on the seach result
UC7QxZdogxV1gloaOBO02wiw Aftonbladet
match found!
*********************
Channel name:  Alternet (www.alternet.org)
channel result found on the seach result
channel result found on the seach result
channel result found on the seach result
UCByDWB-GsSjHnUS5o7Hohsg AlterNet
UC0iBEcQdEurbfEXAtPrF2Vw Viral Alternet
UCLxRAQpUVzC_wFzaT1hpDRg AlterNET Deluxe
*********************
Channel name:  America Blog (americablog.com)
*********************
Channel name:  American Oversight
*********************
Channel name:  Americans United for Separation of Church and State (www.au.org)
*********************
Channel name:  Angry White Men (angrywhitemen.org)
*********************
Channel name:  Attack the System (attackthesystem.com)
channel result found on the seach r

KeyboardInterrupt: 

In [33]:
l = []
for _ in range(5):
    l = list((1, 2, 3))

[1, 2, 3]

In [28]:
def recursive_lookup(k, d):
    # imporvised from https://stackoverflow.com/questions/48314755/find-keys-in-nested-dictionary
    # here, k is the key to search
    # d is the dictonary to find from.
    if k in d: return d[k]
    for v in d.values():
        if isinstance(v, dict):
            a = recursive_lookup(k, v)
            if a is not None: yield a
        elif isinstance(v, list):
            for v_list in v:
                if isinstance(v_list, dict):
                    b = recursive_lookup(k, v_list)
                    if b is not None: yield b
    return None
#recursive_lookup("description", yt_about_page)

In [29]:
def search_dict(partial, key):
    if isinstance(partial, dict):
        for k, v in partial.items():
            if k == key:
                yield v
            else:
                for o in search_dict(v, key):
                    yield o
    elif isinstance(partial, list):
        for i in partial:
            for o in search_dict(i, key):
                yield o


In [11]:
# 6 from the original, 5th from our

In [73]:
def get_youtube_channel_id(service, part_id, youtube_user):
    """
    Get youtube channel id with the given youtube user.
    """
    for i in range(3):
        try:
            response = service.channels().list(part = part_id, forUsername=youtube_user)
            response = response.execute()
            #print(response)
            # if there is a response
            if response is not None:
                if "items" in response:
                    if isinstance(response["items"], list):
                        if len(response["items"][0]) > 0:
                            #print("yes")
                            #print(response["items"][0]["id"])
                            channel_id = response["items"][0]["id"]
                            return channel_id
            else:
                return ""

        except:
            time.sleep(2**i)
            print("exception!")
    return ""

In [75]:
get_youtube_channel_id(youtube_service, "id", "sentdex")

'UCfzlCWGWYyIQ0aLC5w48gBQ'

In [76]:
def check_youtube_channel_id(service, part_id, youtube_id):
    """
    Get youtube channel id with the given youtube user.
    """
    for i in range(3):
        try:
            response = service.channels().list(part = part_id, id=youtube_id)
            response = response.execute()
            #print(response)
            # if there is a response
            if response is not None:
                if "items" in response:
                    if isinstance(response["items"], list):
                        if len(response["items"][0]) > 0:
                            #print("yes")
                            #print(response["items"][0]["id"])
                            channel_id = response["items"][0]["id"]
                            return channel_id
            else:
                return ""
        except:
            time.sleep(2**i)
            print("exception!")
    return ""

In [77]:
check_youtube_channel_id(youtube_service, "id", 'UCfzlCWGWYyIQ0aLC5w48gBQ')

'UCfzlCWGWYyIQ0aLC5w48gBQ'

In [62]:
# for simplicity, for now, we will use csv 3, although it should have been csv 5.
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/3. scrap_youtube_twitter_handle.csv")
channel_yt_twitter.drop("index",axis=1,inplace=True)
channel_yt_twitter

Name  Bias Rating  \
0                                       Accountable.US         left   
1                                      Act.TV (act.tv)         left   
2                                          Aftonbladet         left   
3                                               Al DIA         left   
4             Alliance for Justice (AFJ) (www.afj.org)         left   
5                                             Alt News         left   
6                          Alternet (www.alternet.org)         left   
7                                Amandla (aidc.org.za)         left   
8                       America Blog (americablog.com)         left   
9    American Bridge 21st Century (americanbridgepa...         left   
10                                  American Oversight         left   
11   Americans United for Separation of Church and ...         left   
12                 Angry White Men (angrywhitemen.org)         left   
13             Attack the System (attackthesystem.com)         left   
14                 AutoStraddle (www.autostraddle.com)         left   
15            Baltimore City Paper (www.citypaper.com)         left   
16                    Bay Area Reporter (www.ebar.com)         left   
17                    Being Liberal (www.themaven.net)         left   
18                   BillMoyers.com (billmoyers.com)\n         left   
19                        Bitch Media (bitchmedia.org)         left   
20         Black Agenda Report (blackagendareport.com)         left   
21             Black America Web (blackamericaweb.com)         left   
22           Black Lives Matter (blacklivesmatter.com)         left   
23             Black Main Street (blackmainstreet.net)         left   
24                         BoingBoing (boingboing.net)         left   
25                    Boston Review (bostonreview.net)         left   
26                                          Brut.Media         left   
27                            Bust Magazine (bust.com)         left   
28               Call to Activism (calltoactivism.com)         left   
29              Canada Fact Check (canadafactcheck.ca)         left   
30          Canadian Dimension (canadiandimension.com)         left   
31                 Capital & Main (capitalandmain.com)         left   
32                               Care2 (www.care2.com)         left   
33        Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34   Center for American Progress (www.americanprog...         left   
35    Center for Media and Democracy (www.prwatch.org)         left   
36           Center for a Stateless Society (c4ss.org)         left   
37                Change.org (https://www.change.org/)         left   
38              Chicago Reader (www.chicagoreader.com)         left   
39              Chicago Reporter (chicagoreporter.com)         left   
40    China Internet Information Center (china.org.cn)         left   
41                Citizen Critics (citizencritics.org)         left   
42           Climate Home News (climatechangenews.com)         left   
43                                   CNN (www.cnn.com)         left   
44                        Code Pink (www.codepink.org)         left   
45                         ColorLines (colorlines.com)         left   
46   Columbus Free Press (https://columbusfreepress...         left   
47                                         Comic Sands         left   
48                Common Dreams (www.commondreams.org)         left   
49                   Commune Magazine (communemag.com)         left   
50                            Cop Block (copblock.org)         left   
51                 Cosmopolitan (www.cosmopolitan.com)         left   
52       CounterCurrents.org (www.countercurrents.org)         left   
53                 CounterPunch (www.counterpunch.org)         left   
54                              Crikey (crikey.com.au)         left   
55                         CrimethInc (crimethinc.com)         left   
56 

In [65]:
channel_yt_twitter['Youtube User'] = channel_yt_twitter['Youtube Channel'] 
channel_yt_twitter

Name  Bias Rating  \
0                                       Accountable.US         left   
1                                      Act.TV (act.tv)         left   
2                                          Aftonbladet         left   
3                                               Al DIA         left   
4             Alliance for Justice (AFJ) (www.afj.org)         left   
5                                             Alt News         left   
6                          Alternet (www.alternet.org)         left   
7                                Amandla (aidc.org.za)         left   
8                       America Blog (americablog.com)         left   
9    American Bridge 21st Century (americanbridgepa...         left   
10                                  American Oversight         left   
11   Americans United for Separation of Church and ...         left   
12                 Angry White Men (angrywhitemen.org)         left   
13             Attack the System (attackthesystem.com)         left   
14                 AutoStraddle (www.autostraddle.com)         left   
15            Baltimore City Paper (www.citypaper.com)         left   
16                    Bay Area Reporter (www.ebar.com)         left   
17                    Being Liberal (www.themaven.net)         left   
18                   BillMoyers.com (billmoyers.com)\n         left   
19                        Bitch Media (bitchmedia.org)         left   
20         Black Agenda Report (blackagendareport.com)         left   
21             Black America Web (blackamericaweb.com)         left   
22           Black Lives Matter (blacklivesmatter.com)         left   
23             Black Main Street (blackmainstreet.net)         left   
24                         BoingBoing (boingboing.net)         left   
25                    Boston Review (bostonreview.net)         left   
26                                          Brut.Media         left   
27                            Bust Magazine (bust.com)         left   
28               Call to Activism (calltoactivism.com)         left   
29              Canada Fact Check (canadafactcheck.ca)         left   
30          Canadian Dimension (canadiandimension.com)         left   
31                 Capital & Main (capitalandmain.com)         left   
32                               Care2 (www.care2.com)         left   
33        Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34   Center for American Progress (www.americanprog...         left   
35    Center for Media and Democracy (www.prwatch.org)         left   
36           Center for a Stateless Society (c4ss.org)         left   
37                Change.org (https://www.change.org/)         left   
38              Chicago Reader (www.chicagoreader.com)         left   
39              Chicago Reporter (chicagoreporter.com)         left   
40    China Internet Information Center (china.org.cn)         left   
41                Citizen Critics (citizencritics.org)         left   
42           Climate Home News (climatechangenews.com)         left   
43                                   CNN (www.cnn.com)         left   
44                        Code Pink (www.codepink.org)         left   
45                         ColorLines (colorlines.com)         left   
46   Columbus Free Press (https://columbusfreepress...         left   
47                                         Comic Sands         left   
48                Common Dreams (www.commondreams.org)         left   
49                   Commune Magazine (communemag.com)         left   
50                            Cop Block (copblock.org)         left   
51                 Cosmopolitan (www.cosmopolitan.com)         left   
52       CounterCurrents.org (www.countercurrents.org)         left   
53                 CounterPunch (www.counterpunch.org)         left   
54                              Crikey (crikey.com.au)         left   
55                         CrimethInc (crimethinc.com)         left   
56 

In [68]:
# iterate over the dataframe
for index, row in channel_yt_twitter.iterrows():
    
    channel_id_user = channel_yt_twitter.iloc[index, 4]
    
    if not pd.isna(channel_id_user):
        
        # first, we will call get_youtube_channel_id().
        channel_id_response = get_youtube_channel_id(youtube_service, part, channel_id_user)
        print(channel_id_response)

        if channel_id_response == "":
            print("Cannot find from the first function, trying again from the second function!!!")
            channel_id_response = check_youtube_channel_id(youtube_service, part, channel_id_user)
            print(channel_id_response)
            if channel_id_response == "":
                print("Cannot find from the second function!!!")
            else:
                channel_yt_twitter.iloc[index, 4] = channel_id_response
        else:
            channel_yt_twitter.iloc[index, 4] = channel_id_response


Cannot find from the first function, trying again from the second function!!!

Cannot find from the second function!!!
UCGrUeq1FtRamLqZgaCIgB3w
UC4chaUevLgCVSz-RcgqgoZQ

Cannot find from the first function, trying again from the second function!!!

Cannot find from the second function!!!

Cannot find from the first function, trying again from the second function!!!
UCmX0gITcFMtmDSah8-wCChw
UCsSSZZIwlM9OajvbRSydK2A

Cannot find from the first function, trying again from the second function!!!
UC_WSavcwZVE3ciFM8yCwkBw
UCexetvuR0DbNlprwhe4Ze1g

Cannot find from the first function, trying again from the second function!!!

Cannot find from the second function!!!

Cannot find from the first function, trying again from the second function!!!
UCXu7fg-_KdAoHY7bmahr9vg

Cannot find from the first function, trying again from the second function!!!
UCjfpIrbyc1hMT-CRZWbGF4g
UC0COu43Li7CUL2jseBpH9kQ
UCOA38--mWqKKdCAr6eFy-sA
UCKL_VqV2UqBnmjGy4fLQ24g

Cannot find from the first function, trying agai

In [69]:
channel_yt_twitter

Name  Bias Rating  \
0                                       Accountable.US         left   
1                                      Act.TV (act.tv)         left   
2                                          Aftonbladet         left   
3                                               Al DIA         left   
4             Alliance for Justice (AFJ) (www.afj.org)         left   
5                                             Alt News         left   
6                          Alternet (www.alternet.org)         left   
7                                Amandla (aidc.org.za)         left   
8                       America Blog (americablog.com)         left   
9    American Bridge 21st Century (americanbridgepa...         left   
10                                  American Oversight         left   
11   Americans United for Separation of Church and ...         left   
12                 Angry White Men (angrywhitemen.org)         left   
13             Attack the System (attackthesystem.com)         left   
14                 AutoStraddle (www.autostraddle.com)         left   
15            Baltimore City Paper (www.citypaper.com)         left   
16                    Bay Area Reporter (www.ebar.com)         left   
17                    Being Liberal (www.themaven.net)         left   
18                   BillMoyers.com (billmoyers.com)\n         left   
19                        Bitch Media (bitchmedia.org)         left   
20         Black Agenda Report (blackagendareport.com)         left   
21             Black America Web (blackamericaweb.com)         left   
22           Black Lives Matter (blacklivesmatter.com)         left   
23             Black Main Street (blackmainstreet.net)         left   
24                         BoingBoing (boingboing.net)         left   
25                    Boston Review (bostonreview.net)         left   
26                                          Brut.Media         left   
27                            Bust Magazine (bust.com)         left   
28               Call to Activism (calltoactivism.com)         left   
29              Canada Fact Check (canadafactcheck.ca)         left   
30          Canadian Dimension (canadiandimension.com)         left   
31                 Capital & Main (capitalandmain.com)         left   
32                               Care2 (www.care2.com)         left   
33        Ceasefire Magazine (ceasefiremagazine.co.uk)         left   
34   Center for American Progress (www.americanprog...         left   
35    Center for Media and Democracy (www.prwatch.org)         left   
36           Center for a Stateless Society (c4ss.org)         left   
37                Change.org (https://www.change.org/)         left   
38              Chicago Reader (www.chicagoreader.com)         left   
39              Chicago Reporter (chicagoreporter.com)         left   
40    China Internet Information Center (china.org.cn)         left   
41                Citizen Critics (citizencritics.org)         left   
42           Climate Home News (climatechangenews.com)         left   
43                                   CNN (www.cnn.com)         left   
44                        Code Pink (www.codepink.org)         left   
45                         ColorLines (colorlines.com)         left   
46   Columbus Free Press (https://columbusfreepress...         left   
47                                         Comic Sands         left   
48                Common Dreams (www.commondreams.org)         left   
49                   Commune Magazine (communemag.com)         left   
50                            Cop Block (copblock.org)         left   
51                 Cosmopolitan (www.cosmopolitan.com)         left   
52       CounterCurrents.org (www.countercurrents.org)         left   
53                 CounterPunch (www.counterpunch.org)         left   
54                              Crikey (crikey.com.au)         left   
55                         CrimethInc (crimethinc.com)         left   
56 

In [13]:
# 7th from original, 6th from ours.

In [89]:
def ajax_request(session, url, params=None, data=None, headers=None, max_retry=5, sleep=20):
    for idx_request in range(max_retry):
        response = session.post(url, params=params, data=data, headers=headers)
        time.sleep(1)
        if response.status_code == 200:
            ret_json = response.json()
            if isinstance(ret_json, list):
                ret_json = [x for x in ret_json if 'response' in x][0]
            ret_json.update({'num_request': idx_request + 1})
            return ret_json
        elif response.status_code in [403, 413]:
            return {'error': 'Comments are turned off', 'num_request': idx_request + 1}
        time.sleep(sleep)
    return {'error': 'Unknown error {0}'.format(response.status_code), 'num_request': max_retry}

In [ ]:
# for simplicity, for now, we will use csv 3, although it should have been csv 5.
channel_yt_twitter = pd.read_csv("D:/MSc Data Science/Elective Modules - Research Modules/[INF-DS-RMB] Research Module B/RM Code/Sentiment-Classification-Youtube-Comments-Political-Affiliation/data/3. scrap_youtube_twitter_handle.csv")
channel_yt_twitter.drop("index",axis=1,inplace=True)
channel_yt_twitter

In [16]:
"Accountable.US,left,left4.png,USA,https://www.accountable.us/,accountable.us".rstrip().split(',')[-1]

'accountable.us'

In [17]:
"UCGrUeq1FtRamLqZgaCIgB3w"[2:]

'GrUeq1FtRamLqZgaCIgB3w'

In [75]:

#https://www.youtube.com/playlist?list=UUpontealdiatv
# channel id from "pontealdiatv"
channel_d = "UCGrUeq1FtRamLqZgaCIgB3w"

# to scrap all the videos information from a single channel, 
channel_all_videos_playlist = "UU" + channel_d[2:]

In [76]:
header = {"User-Agent": "Mozilla/5.0 (compatible; Googlebot/2.1; +http://www.google.com/bot.html)"}
response = requests.get("https://www.youtube.com/playlist?list={}".format(channel_all_videos_playlist), headers=header)

In [77]:
soup = BeautifulSoup(response.text, features='html.parser')
aid = soup.find('script',string=re.compile('ytInitialData')).text
aid = json.loads(aid[20:-1])

In [78]:
aid

{'responseContext': {'serviceTrackingParams': [{'service': 'GFEEDBACK',
    'params': [{'key': 'browse_id', 'value': 'VLUUGrUeq1FtRamLqZgaCIgB3w'},
     {'key': 'logged_in', 'value': '0'},
     {'key': 'e',
      'value': '24002022,24166867,23744176,9407156,24200175,23918597,24219713,24165080,24181174,24198739,24185349,24186508,24082662,23804281,24169501,24218143,24196597,23966208,24187516,24214554,24080738,24210094,24208721,24167177,24120819,23986031,24034168,24163012,24215196,24152442,1714250,24001373,24211628,24191629,24219034,23998056,24187043,23934970,24085811,23882503,24166247,24036947,24185614,24135310,23983296,24187377,24189951,24199724,24199710,24138442,24140247,24164186,24077266,23946420,24002025,24077241,24007246,24211177,24004644,9406122,24199774,24212037'}]},
   {'service': 'GOOGLE_HELP',
    'params': [{'key': 'browse_id', 'value': 'VLUUGrUeq1FtRamLqZgaCIgB3w'}]},
   {'service': 'CSI',
    'params': [{'key': 'c', 'value': 'WEB'},
     {'key': 'cver', 'value': '2.20220524.

In [79]:
content = aid["contents"]["twoColumnBrowseResultsRenderer"]["tabs"][0]["tabRenderer"]["content"]["sectionListRenderer"]["contents"][0]["itemSectionRenderer"]["contents"][0]["playlistVideoListRenderer"]["contents"]
#content

In [84]:
content[100]

{'continuationItemRenderer': {'trigger': 'CONTINUATION_TRIGGER_ON_ITEM_SHOWN',
  'continuationEndpoint': {'clickTrackingParams': 'CCQQ7zsYACITCJSoiaak-fcCFQ-dewodoZ0M2A==',
   'commandMetadata': {'webCommandMetadata': {'sendPost': True,
     'apiUrl': '/youtubei/v1/browse'}},
   'continuationCommand': {'token': '4qmFsgJNEhpWTFVVR3JVZXExRnRSYW1McVpnYUNJZ0IzdxoUQ0FGNkJsQlVPa05IVVElM0QlM0SaAhhVVUdyVWVxMUZ0UmFtTHFaZ2FDSWdCM3c%3D',
    'request': 'CONTINUATION_REQUEST_TYPE_BROWSE'}}}}

In [88]:
playlist_video_id = []
for i, c in enumerate(content):
    print(i)
    #print(c["playlistVideoRenderer"]["videoId"])
    
    
    if "continuationItemRenderer" in c:
        if c["continuationItemRenderer"] is not None:
            print(c["continuationItemRenderer"])
    #playlist_video_id.append(c["playlistVideoRenderer"]["videoId"])
    
    if ncd:
        continuations = [(ncd['continuationCommand']['token'], ncd['clickTrackingParams'])]

        while continuations:
            continuation, itct = continuations.pop()
            response_json = ajax_request(session,
                                         YOUTUBE_BROWSER_AJAX_URL,
                                         params={'referer': YOUTUBE_PLAYLIST_URL.format(playlist_id=playlist_id),
                                                 'pbj': 1,
                                                 'ctoken': continuation,
                                                 'continuation': continuation,
                                                 'itct': itct},
                                         data={'session_token': session_token},
                                         headers={'X-YouTube-Client-Name': '1',
                                                  'X-YouTube-Client-Version': '2.20200207.03.01'})

            if len(response_json) == 0:
                break
            if next(search_dict(response_json, 'externalErrorMessage'), None):
                raise Exception('Error returned from server: ' + next(search_dict(response_json, 'externalErrorMessage')))
            elif 'error' in response_json:
                raise Exception(response_json['error'])

            # Ordering matters. The newest continuations should go first.
            continuations = [(ncd['continuationCommand']['token'], ncd['clickTrackingParams']) for ncd in search_dict(response_json, 'continuationEndpoint')] + continuations

            for video in search_dict(response_json, 'playlistVideoRenderer'):
                playlist_videos.append(video['videoId'])

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
{'trigger': 'CONTINUATION_TRIGGER_ON_ITEM_SHOWN', 'continuationEndpoint': {'clickTrackingParams': 'CCQQ7zsYACITCJSoiaak-fcCFQ-dewodoZ0M2A==', 'commandMetadata': {'webCommandMetadata': {'sendPost': True, 'apiUrl': '/youtubei/v1/browse'}}, 'continuationCommand': {'token': '4qmFsgJNEhpWTFVVR3JVZXExRnRSYW1McVpnYUNJZ0IzdxoUQ0FGNkJsQlVPa05IVVElM0QlM0SaAhhVVUdyVWVxMUZ0UmFtTHFaZ2FDSWdCM3c%3D', 'request': 'CONTINUATION_REQUEST_TYPE_BROWSE'}}}


KeyError: 'playlistVideoRenderer'

In [74]:
playlist_video_id

['7p-BOlIG664',
 'Wjg0AX8sjLk',
 '2665Qu_UJvc',
 'DsfjPosC42g',
 'p8gQ7Qsm488',
 'HsKLFScQIHk',
 'aovhu5SUgxs',
 'O-QURjL1twE',
 'B7TrdnMi3F4',
 '9FeESr-AYEU']

In [ ]:
https://www.youtube.com/watch?v=7p-BOlIG664